# Flow of Machine Learning

<br />

I use the "Home Credit Default Risk" competition on Kaggle.


https://www.kaggle.com/c/home-credit-default-risk

## [Task 1] Cross-validation

In [2]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import lightgbm as lgbm
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import KFold
from sklearn.model_selection import GridSearchCV

# featuretools for automated feature engineering
import featuretools as ft

# Suppress warnings from pandas
import warnings
warnings.filterwarnings('ignore')

In [2]:
# Def of computing the AUC

def compute_auc(train_test):
    # split the concatenated dataset into the train dataset and the test dataset
    train_input = train_test[0: train.shape[0]].copy()
    test_input = train_test[train.shape[0]:].copy()
    
    X = train_input.drop("TARGET",axis=1).values
    y = train_input.loc[:,'TARGET'].values
    
    # LightGBM
    lgbm_train = lgbm.Dataset(X,y)
    lgbm_eval = lgbm.Dataset(X, y, reference=lgbm_train)
    lgbm_params = {'objective':'binary',
                   'boosting_type': 'rf',
                   'subsample': 0.623,
                   'colsample_bytree': 0.7,
                   'num_leaves': 127,
                   'max_depth': 8,
                   'seed': 99,
                   'bagging_freq': 1,
                   'n_jobs': 4}
    
    model = lgbm.train(lgbm_params, lgbm_train, valid_sets=lgbm_eval)
    
    # Predict the test dataset
    y_pred = model.predict(X)
    
    # Compute the AUC
    return roc_auc_score(y,y_pred), X, y, lgbm_params

## [Task 2] GridSearch

## [Task 3] Research Useful Tips on Kernels

<br />

- "Automated Feature Engineering Basics"


https://www.kaggle.com/willkoehrsen/automated-feature-engineering-basics

    - It is possible to increase features automatically by referring to the kernel.


- "Feature Selection with Null Importances"


https://www.kaggle.com/ogrellier/feature-selection-with-null-importances

    - I am able to score features by several ways and check the impact of removing uncorrelated features.

## [Task 4] Create Models of High-Generalization Performance

In [3]:
# Get main datasets

# The train and  test dataset
train = pd.read_csv('"Home Credit Default Risk".application_train.csv')
test = pd.read_csv('"Home Credit Default Risk".application_test.csv')

# Additional datasets
bureau = pd.read_csv('"Home Credit Default Risk".bureau.csv')
bureau_balance = pd.read_csv('"Home Credit Default Risk".bureau_balance.csv')
credit = pd.read_csv('"Home Credit Default Risk".credit_card_balance.csv')
installments = pd.read_csv('"Home Credit Default Risk".installments_payments.csv')
cash = pd.read_csv('"Home Credit Default Risk".POS_CASH_balance.csv')
previous = pd.read_csv('"Home Credit Default Risk".previous_application.csv')

In [5]:
# Join the train and test set together but add a separate column identifying the set

# Add identifying column
train['set'] = 'train'
test['set'] = 'test'
test["TARGET"] = np.nan

# Append the dataframes
train_test = train.append(test, ignore_index = True)

In [6]:
# Create dummies

new_train_test = pd.get_dummies(train_test)

### Entities and Entitysets

<br />

First, I will make an empty entityset named clients to keep track of all the data.

In [7]:
# Entity set with id applications

es = ft.EntitySet(id = 'clients')

Now I define each entity, or table of data. I need to pass in an index if the data has one or make_index = True if not. Featuretools will automatically infer the types of variables, but I can also change them if needed.

In [8]:
# Entities with a unique index
es = es.entity_from_dataframe(entity_id = 'new_train_test', dataframe = new_train_test, 
                              index = 'SK_ID_CURR')
es = es.entity_from_dataframe(entity_id = 'bureau', dataframe = bureau, index = 'SK_ID_BUREAU')
es = es.entity_from_dataframe(entity_id = 'previous', dataframe = previous, index = 'SK_ID_PREV')

# Entities that do not have a unique index
es = es.entity_from_dataframe(entity_id = 'bureau_balance', dataframe = bureau_balance, 
                              make_index = True, index = 'bureaubalance_index')
es = es.entity_from_dataframe(entity_id = 'cash', dataframe = cash, 
                              make_index = True, index = 'cash_index')
es = es.entity_from_dataframe(entity_id = 'installments', dataframe = installments,
                              make_index = True, index = 'installments_index')
es = es.entity_from_dataframe(entity_id = 'credit', dataframe = credit,
                              make_index = True, index = 'credit_index')

### Relationships

<br />

Relationships are a fundamental concept not only in featuretools, but in any relational database. The best way to think of a one-to-many relationship is with the analogy of parent-to-child. A parent is a single individual, but can have mutliple children. The children can then have multiple children of their own. In a parent table, each individual has a single row. Each individual in the parent table can have multiple rows in the child table.

In [9]:
print('Parent: new_train_test, Parent Variable: SK_ID_CURR\n\n', new_train_test.iloc[:, 111:115].head())
print('\nChild: bureau, Child Variable: SK_ID_CURR\n\n', bureau.iloc[10:30, :4].head())

Parent: new_train_test, Parent Variable: SK_ID_CURR

    FLAG_OWN_CAR_N  FLAG_OWN_CAR_Y  FLAG_OWN_REALTY_N  FLAG_OWN_REALTY_Y
0               1               0                  0                  1
1               1               0                  1                  0
2               0               1                  0                  1
3               1               0                  0                  1
4               1               0                  0                  1

Child: bureau, Child Variable: SK_ID_CURR

     SK_ID_CURR  SK_ID_BUREAU CREDIT_ACTIVE CREDIT_CURRENCY
10      162297       5714472        Active      currency 1
11      162297       5714473        Closed      currency 1
12      162297       5714474        Active      currency 1
13      402440       5714475        Active      currency 1
14      238881       5714482        Closed      currency 1


    - The "SK_ID_CURR" "100002" has one row in the parent table and multiple rows in the child.

    - Two tables are linked via a shared variable. The "new_train_test" and "bureau" dataframe are linked by the "SK_ID_CURR" variable while the "bureau" and "bureau_balance" dataframes are linked with the "SK_ID_BUREAU". Defining the relationships is relatively straightforward, and the diagram provided by the competition is helpful for seeing the relationships. For each relationship, I need to specify the parent variable and the child variable. Altogether, there are a total of 6 relationships between the tables. Below I specify all six relationships and then add them to the EntitySet.

In [10]:
# Relationship between app and bureau
r_new_train_test_bureau = ft.Relationship(es['new_train_test']['SK_ID_CURR'], es['bureau']['SK_ID_CURR'])

# Relationship between bureau and bureau balance
r_bureau_balance = ft.Relationship(es['bureau']['SK_ID_BUREAU'], es['bureau_balance']['SK_ID_BUREAU'])

# Relationship between current app and previous apps
r_new_train_test_previous = ft.Relationship(es['new_train_test']['SK_ID_CURR'], 
                                            es['previous']['SK_ID_CURR'])

# Relationships between previous apps and cash, installments, and credit
r_previous_cash = ft.Relationship(es['previous']['SK_ID_PREV'], es['cash']['SK_ID_PREV'])
r_previous_installments = ft.Relationship(es['previous']['SK_ID_PREV'], es['installments']['SK_ID_PREV'])
r_previous_credit = ft.Relationship(es['previous']['SK_ID_PREV'], es['credit']['SK_ID_PREV'])

In [11]:
# Add in the defined relationships
es = es.add_relationships([r_new_train_test_bureau, r_bureau_balance, r_new_train_test_previous,
                           r_previous_cash, r_previous_installments, r_previous_credit])

# Print out the EntitySet
es

Entityset: clients
  Entities:
    new_train_test [Rows: 356255, Columns: 248]
    bureau [Rows: 1716428, Columns: 17]
    previous [Rows: 1670214, Columns: 37]
    bureau_balance [Rows: 27299925, Columns: 4]
    cash [Rows: 10001358, Columns: 9]
    installments [Rows: 13605401, Columns: 9]
    credit [Rows: 3840312, Columns: 24]
  Relationships:
    bureau.SK_ID_CURR -> new_train_test.SK_ID_CURR
    bureau_balance.SK_ID_BUREAU -> bureau.SK_ID_BUREAU
    previous.SK_ID_CURR -> new_train_test.SK_ID_CURR
    cash.SK_ID_PREV -> previous.SK_ID_PREV
    installments.SK_ID_PREV -> previous.SK_ID_PREV
    credit.SK_ID_PREV -> previous.SK_ID_PREV

### Feature Primitives

<br />

A feature primitive is an operation applied to a table or a set of tables to create a feature. These represent simple calculations, many of which I already use in manual feature engineering, that can be stacked on top of each other to create complex features. Feature primitives fall into two categories:

- Aggregation: function that groups together child datapoints for each parent and then calculates a statistic such as mean, min, max, or standard deviation. An example is calculating the maximum previous loan amount for each client. An aggregation works across multiple tables using relationships between tables.

- Transformation: an operation applied to one or more columns in a single table. An example would be taking the absolute value of a column, or finding the difference between two columns in one table.

<br />

A list of the available features primitives in featuretools can be viewed below.

In [12]:
# List the primitives in a dataframe

primitives = ft.list_primitives()
pd.options.display.max_colwidth = 100
primitives[primitives['type'] == 'aggregation'].head(10)

name         type  \
0             trend  aggregation   
1               sum  aggregation   
2        num_unique  aggregation   
3              skew  aggregation   
4      percent_true  aggregation   
5   time_since_last  aggregation   
6             count  aggregation   
7               max  aggregation   
8               all  aggregation   
9  avg_time_between  aggregation   

                                       description  
0  Finds the number of 'True' values in a boolean.  
1  Finds the number of 'True' values in a boolean.  
2  Finds the number of 'True' values in a boolean.  
3  Finds the number of 'True' values in a boolean.  
4  Finds the number of 'True' values in a boolean.  
5  Finds the number of 'True' values in a boolean.  
6  Finds the number of 'True' values in a boolean.  
7  Finds the number of 'True' values in a boolean.  
8  Finds the number of 'True' values in a boolean.  
9  Finds the number of 'True' values in a boolean.

In [13]:
primitives[primitives['type'] == 'transform'].head(10)

name       type description
19                   numwords  transform            
20      divide_numeric_scalar  transform            
21        time_since_previous  transform            
22               equal_scalar  transform            
23                    is_null  transform            
24                  longitude  transform            
25                    weekday  transform            
26    multiply_numeric_scalar  transform            
27  less_than_equal_to_scalar  transform            
28                 percentile  transform

### Deep Feature Synthesis

<br />

Deep Feature Synthesis (DFS) is the process featuretools uses to make new features. DFS stacks feature primitives to form features with a "depth" equal to the number of primitives.

#### DFS with Default Primitives

In [14]:
# Default primitives from featuretools
default_agg_primitives =  ["sum", "std", "max", "skew", "min", "mean", "count", "percent_true", 
                           "num_unique", "mode"]
default_trans_primitives =  ["day", "year", "month", "weekday", "haversine", "numwords", "characters"]

# DFS with specified primitives
feature_names = ft.dfs(entityset = es, target_entity = 'new_train_test',
                       trans_primitives = default_trans_primitives,
                       agg_primitives=default_agg_primitives, 
                       max_depth = 2, features_only=True)

print('%d Total Features' % len(feature_names))

1822 Total Features


To generate a subset of the features, run the code cell below.

#### DFS with Selected Aggregation Primitives

<br />

The next call I make will specify a smaller set of features. I still am not using much domain knowledge, but this feature set will be more manageable. The next step from here is improving the features I actually build and performing feature selection.

#### 1st Try

In [20]:
# Specify the aggregation primitives
feature_matrix_spec, feature_names_spec = ft.dfs(entityset = es, target_entity = 'new_train_test', 
                                                 agg_primitives = ['sum', 'count', 'mean'], 
                                                 max_depth = 2, features_only = False, verbose = True)

Built 494 features



Elapsed: 00:00 | Remaining: ? | Progress:   0%|          | Calculated: 0/11 chunks


Elapsed: 00:31 | Remaining: 05:16 | Progress:   9%|▉         | Calculated: 1/11 chunks


Elapsed: 00:55 | Remaining: 04:25 | Progress:  18%|█▊        | Calculated: 2/11 chunks


Elapsed: 01:19 | Remaining: 03:41 | Progress:  27%|██▋       | Calculated: 3/11 chunks


Elapsed: 01:42 | Remaining: 03:03 | Progress:  36%|███▋      | Calculated: 4/11 chunks


Elapsed: 02:03 | Remaining: 02:28 | Progress:  45%|████▌     | Calculated: 5/11 chunks


Elapsed: 02:27 | Remaining: 02:03 | Progress:  55%|█████▍    | Calculated: 6/11 chunks


Elapsed: 02:50 | Remaining: 01:36 | Progress:  64%|██████▎   | Calculated: 7/11 chunks


Elapsed: 03:13 | Remaining: 01:10 | Progress:  73%|███████▎  | Calculated: 8/11 chunks


Elapsed: 03:35 | Remaining: 00:46 | Progress:  82%|████████▏ | Calculated: 9/11 chunks


Elapsed: 03:58 | Remaining: 00:23 | Progress:  91%|█████████ | Calculated: 10/11 chunks


El

In [22]:
feature_names[-20:]

[<Feature: MEAN(previous.MEAN(credit.AMT_DRAWINGS_POS_CURRENT))>,
 <Feature: MEAN(previous.MEAN(credit.AMT_INST_MIN_REGULARITY))>,
 <Feature: MEAN(previous.MEAN(credit.AMT_PAYMENT_CURRENT))>,
 <Feature: MEAN(previous.MEAN(credit.AMT_PAYMENT_TOTAL_CURRENT))>,
 <Feature: MEAN(previous.MEAN(credit.AMT_RECEIVABLE_PRINCIPAL))>,
 <Feature: MEAN(previous.MEAN(credit.AMT_RECIVABLE))>,
 <Feature: MEAN(previous.MEAN(credit.AMT_TOTAL_RECEIVABLE))>,
 <Feature: MEAN(previous.MEAN(credit.CNT_DRAWINGS_ATM_CURRENT))>,
 <Feature: MEAN(previous.MEAN(credit.CNT_DRAWINGS_CURRENT))>,
 <Feature: MEAN(previous.MEAN(credit.CNT_DRAWINGS_OTHER_CURRENT))>,
 <Feature: MEAN(previous.MEAN(credit.CNT_DRAWINGS_POS_CURRENT))>,
 <Feature: MEAN(previous.MEAN(credit.CNT_INSTALMENT_MATURE_CUM))>,
 <Feature: MEAN(previous.MEAN(credit.SK_DPD))>,
 <Feature: MEAN(previous.MEAN(credit.SK_DPD_DEF))>,
 <Feature: MEAN(previous.COUNT(credit))>,
 <Feature: MEAN(previous.NUM_UNIQUE(credit.NAME_CONTRACT_STATUS))>,
 <Feature: NUM_UNIQ

In [21]:
# display the 1000 columns without omitting
pd.options.display.max_columns = 1000

feature_matrix_spec.head(10)

AMT_ANNUITY  AMT_CREDIT  AMT_GOODS_PRICE  AMT_INCOME_TOTAL  \
SK_ID_CURR                                                               
100001          20560.5    568800.0         450000.0          135000.0   
100002          24700.5    406597.5         351000.0          202500.0   
100003          35698.5   1293502.5        1129500.0          270000.0   
100004           6750.0    135000.0         135000.0           67500.0   
100005          17370.0    222768.0         180000.0           99000.0   
100006          29686.5    312682.5         297000.0          135000.0   
100007          21865.5    513000.0         513000.0          121500.0   
100008          27517.5    490495.5         454500.0           99000.0   
100009          41301.0   1560726.0        1395000.0          171000.0   
100010          42075.0   1530000.0        1530000.0          360000.0   

            AMT_REQ_CREDIT_BUREAU_DAY  AMT_REQ_CREDIT_BUREAU_HOUR  \
SK_ID_CURR                                                          
100001                            0.0                         0.0   
100002                            0.0                         0.0   
100003                            0.0                         0.0   
100004                            0.0                         0.0   
100005                            0.0                         0.0   
100006                            NaN                         NaN   
100007                            0.0                         0.0   
100008                            0.0                         0.0   
100009                            0.0                         0.0   
100010                            0.0                         0.0   

            AMT_REQ_CREDIT_BUREAU_MON  AMT_REQ_CREDIT_BUREAU_QRT  \
SK_ID_CURR                                                         
100001                            0.0                        0.0   
100002                            0.0                        0.0   
100003                            0.0                        0.0   
100004                            0.0                        0.0   
100005                            0.0                        0.0   
100006                            NaN                        NaN   
100007                            0.0                        0.0   
100008                            0.0                        1.0   
100009                            1.0                        1.0   
100010                            0.0                        0.0   

            AMT_REQ_CREDIT_BUREAU_WEEK  AMT_REQ_CREDIT_BUREAU_YEAR  \
SK_ID_CURR                                                           
100001                             0.0                         0.0   
100002                             0.0                         1.0   
100003                             0.0                         0.0   
100004                             0.0                         0.0   
100005                             0.0                         3.0   
100006                             NaN                         NaN   
100007                             0.0                         0.0   
100008                             0.0                         1.0   
100009                             0.0                         2.0   
100010                             0.0                         0.0   

            APARTMENTS_AVG  APARTMENTS_MEDI  APARTMENTS_MODE  \
SK_ID_CURR                                                     
100001              0.0660           0.0666           0.0672   
100002              0.0247           0.0250           0.0252   
100003              0.0959           0.0968           0.0924   
100004                 NaN              NaN              NaN   
100005                 NaN              NaN              NaN   
100006                 NaN              NaN              NaN   
100007                 NaN              NaN              NaN   
100008                 NaN              NaN              NaN

In [78]:
feature_matrix_spec.set_train

SK_ID_CURR
100001    0
100002    1
100003    1
100004    1
100005    0
100006    1
100007    1
100008    1
100009    1
100010    1
100011    1
100012    1
100013    0
100014    1
100015    1
100016    1
100017    1
100018    1
100019    1
100020    1
100021    1
100022    1
100023    1
100024    1
100025    1
100026    1
100027    1
100028    0
100029    1
100030    1
         ..
456226    1
456227    1
456228    1
456229    1
456230    1
456231    1
456232    1
456233    1
456234    1
456235    1
456236    1
456237    1
456238    1
456239    1
456240    1
456241    1
456242    1
456243    1
456244    1
456245    1
456246    1
456247    1
456248    1
456249    1
456250    0
456251    1
456252    1
456253    1
456254    1
456255    1
Name: set_train, Length: 356255, dtype: uint8

In [79]:
feature_matrix_spec.set_test

SK_ID_CURR
100001    1
100002    0
100003    0
100004    0
100005    1
100006    0
100007    0
100008    0
100009    0
100010    0
100011    0
100012    0
100013    1
100014    0
100015    0
100016    0
100017    0
100018    0
100019    0
100020    0
100021    0
100022    0
100023    0
100024    0
100025    0
100026    0
100027    0
100028    1
100029    0
100030    0
         ..
456226    0
456227    0
456228    0
456229    0
456230    0
456231    0
456232    0
456233    0
456234    0
456235    0
456236    0
456237    0
456238    0
456239    0
456240    0
456241    0
456242    0
456243    0
456244    0
456245    0
456246    0
456247    0
456248    0
456249    0
456250    1
456251    0
456252    0
456253    0
456254    0
456255    0
Name: set_test, Length: 356255, dtype: uint8

In [66]:
# Split the concatenated dataset into the train dataset and the test dataset

train_input = feature_matrix_spec[feature_matrix_spec.set_train==1].copy()
test_input = feature_matrix_spec[feature_matrix_spec.set_train==0].copy()

In [74]:
X = train_input.drop("TARGET",axis=1).values
y = train_input.loc[:,'TARGET'].values

In [75]:
# LightGBM

lgbm_train = lgbm.Dataset(X,y)
lgbm_eval = lgbm.Dataset(X, y, reference=lgbm_train)
lgbm_params = {'objective':'binary',
               'boosting_type': 'rf',
               'subsample': 0.623,
               'colsample_bytree': 0.7,
               'num_leaves': 127,
               'max_depth': 8,
               'seed': 99,
               'bagging_freq': 1,
               'n_jobs': 4}

model = lgbm.train(lgbm_params, lgbm_train, valid_sets=lgbm_eval)

[1]	valid_0's binary_logloss: 0.260009
[2]	valid_0's binary_logloss: 0.251242
[3]	valid_0's binary_logloss: 0.251121
[4]	valid_0's binary_logloss: 0.249065
[5]	valid_0's binary_logloss: 0.248279
[6]	valid_0's binary_logloss: 0.247879
[7]	valid_0's binary_logloss: 0.24768
[8]	valid_0's binary_logloss: 0.247366
[9]	valid_0's binary_logloss: 0.247128
[10]	valid_0's binary_logloss: 0.247105
[11]	valid_0's binary_logloss: 0.246951
[12]	valid_0's binary_logloss: 0.246955
[13]	valid_0's binary_logloss: 0.246841
[14]	valid_0's binary_logloss: 0.246945
[15]	valid_0's binary_logloss: 0.247005
[16]	valid_0's binary_logloss: 0.246902
[17]	valid_0's binary_logloss: 0.247004
[18]	valid_0's binary_logloss: 0.247032
[19]	valid_0's binary_logloss: 0.2471
[20]	valid_0's binary_logloss: 0.246945
[21]	valid_0's binary_logloss: 0.246833
[22]	valid_0's binary_logloss: 0.246871
[23]	valid_0's binary_logloss: 0.246817
[24]	valid_0's binary_logloss: 0.246734
[25]	valid_0's binary_logloss: 0.246662
[26]	valid_0

In [76]:
# Predict the test dataset

y_pred = model.predict(X)

In [77]:
# Compute the AUC

roc_auc_score(y,y_pred)

0.765151007420907

In [83]:
# Predict the test dataset
y_test_pred = model.predict(test_input.values, num_iteration=model.best_iteration)

# Submittion the result
sub = pd.read_csv('"Home Credit Default Risk".sample_submission.csv')

sub['TARGET'] = y_test_pred

sub.to_csv('"Home Credit Default Risk"_pipeline2-1.csv', index=False)   # I need to set a file name here

#### 2nd Try

In [84]:
# Check the contents

feature_matrix_spec

AMT_ANNUITY  AMT_CREDIT  AMT_GOODS_PRICE  AMT_INCOME_TOTAL  \
SK_ID_CURR                                                               
100001          20560.5    568800.0         450000.0        135000.000   
100002          24700.5    406597.5         351000.0        202500.000   
100003          35698.5   1293502.5        1129500.0        270000.000   
100004           6750.0    135000.0         135000.0         67500.000   
100005          17370.0    222768.0         180000.0         99000.000   
100006          29686.5    312682.5         297000.0        135000.000   
100007          21865.5    513000.0         513000.0        121500.000   
100008          27517.5    490495.5         454500.0         99000.000   
100009          41301.0   1560726.0        1395000.0        171000.000   
100010          42075.0   1530000.0        1530000.0        360000.000   
100011          33826.5   1019610.0         913500.0        112500.000   
100012          20250.0    405000.0         405000.0        135000.000   
100013          69777.0    663264.0         630000.0        202500.000   
100014          21177.0    652500.0         652500.0        112500.000   
100015          10678.5    148365.0         135000.0         38419.155   
100016           5881.5     80865.0          67500.0         67500.000   
100017          28966.5    918468.0         697500.0        225000.000   
100018          32778.0    773680.5         679500.0        189000.000   
100019          20160.0    299772.0         247500.0        157500.000   
100020          26149.5    509602.5         387000.0        108000.000   
100021          13500.0    270000.0         270000.0         81000.000   
100022           7875.0    157500.0         157500.0        112500.000   
100023          17563.5    544491.0         454500.0         90000.000   
100024          21375.0    427500.0         427500.0        135000.000   
100025          37561.5   1132573.5         927000.0        202500.000   
100026          32521.5    497520.0         450000.0        450000.000   
100027          23850.0    239850.0         225000.0         83250.000   
100028          49018.5   1575000.0        1575000.0        315000.000   
100029          12703.5    247500.0         247500.0        135000.000   
100030          11074.5    225000.0         225000.0         90000.000   
...                 ...         ...              ...               ...   
456226          34969.5    500566.5         472500.0        225000.000   
456227          16479.0    247275.0         225000.0         99000.000   
456228          35617.5    545040.0         450000.0        540000.000   
456229           9000.0    180000.0         180000.0        270000.000   
456230          18283.5    355536.0         270000.0        292500.000   
456231          31473.0   1071909.0         936000.0        117000.000   
456232          13351.5    135000.0         135000.0        157500.000   
456233          23089.5    521280.0         450000.0        225000.000   
456234           9148.5    135000.0         135000.0         81000.000   
456235          31522.5   1078200.0         900000.0         90000.000   
456236          43443.0   1575000.0        1575000.0        585000.000   
456237          37678.5    946764.0         765000.0        135000.000   
456238          46858.5    479700.0         450000.0        270000.000   
456239          23773.5    808650.0         675000.0        180000.000   
456240          16875.0    337500.0         337500.0        360000.000   
456241          12028.5    270126.0         193500.0        180000.000   
456242          52168.5   1312110.0        1125000.0        198000.000   
456243          12694.5    225000.0         225000.0         81000.000   
456244          35982.0   1303812.0        1138500.0        261000.000   
456245          11871.0    269550.0         225000.0         81000.000   
456246          10620.0    225000.0         225000.0         94500.000   
456247          

In [85]:
feature_matrix_spec.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 356255 entries, 100001 to 456255
Columns: 494 entries, AMT_ANNUITY to MEAN(previous.MEAN(credit.SK_DPD_DEF))
dtypes: float64(313), int64(39), uint8(142)
memory usage: 1007.7 MB


In [86]:
feature_matrix_spec.describe()

AMT_ANNUITY    AMT_CREDIT  AMT_GOODS_PRICE  AMT_INCOME_TOTAL  \
count  356219.000000  3.562550e+05     3.559770e+05      3.562550e+05   
mean    27425.560657  5.877674e+05     5.280200e+05      1.701161e+05   
std     14732.808190  3.986237e+05     3.660650e+05      2.235068e+05   
min      1615.500000  4.500000e+04     4.050000e+04      2.565000e+04   
25%     16731.000000  2.700000e+05     2.340000e+05      1.125000e+05   
50%     25078.500000  5.002110e+05     4.500000e+05      1.530000e+05   
75%     34960.500000  7.975575e+05     6.750000e+05      2.025000e+05   
max    258025.500000  4.050000e+06     4.050000e+06      1.170000e+08   

       AMT_REQ_CREDIT_BUREAU_DAY  AMT_REQ_CREDIT_BUREAU_HOUR  \
count              308687.000000               308687.000000   
mean                    0.006281                    0.005808   
std                     0.104250                    0.079736   
min                     0.000000                    0.000000   
25%                     0.000000                    0.000000   
50%                     0.000000                    0.000000   
75%                     0.000000                    0.000000   
max                     9.000000                    4.000000   

       AMT_REQ_CREDIT_BUREAU_MON  AMT_REQ_CREDIT_BUREAU_QRT  \
count              308687.000000              308687.000000   
mean                    0.231697                   0.304399   
std                     0.855949                   0.786915   
min                     0.000000                   0.000000   
25%                     0.000000                   0.000000   
50%                     0.000000                   0.000000   
75%                     0.000000                   0.000000   
max                    27.000000                 261.000000   

       AMT_REQ_CREDIT_BUREAU_WEEK  AMT_REQ_CREDIT_BUREAU_YEAR  APARTMENTS_AVG  \
count               308687.000000               308687.000000   176307.000000   
mean                     0.029995                    1.911564        0.118138   
std                      0.191374                    1.865338        0.108954   
min                      0.000000                    0.000000        0.000000   
25%                      0.000000                    0.000000        0.057700   
50%                      0.000000                    1.000000        0.088000   
75%                      0.000000                    3.000000        0.148500   
max                      8.000000                   25.000000        1.000000   

       APARTMENTS_MEDI  APARTMENTS_MODE  BASEMENTAREA_AVG  BASEMENTAREA_MEDI  \
count    176307.000000    176307.000000     148671.000000      148671.000000   
mean          0.118549         0.114914          0.088673           0.088178   
std           0.109824         0.108745          0.082312           0.082017   
min           0.000000         0.000000          0.000000           0.000000   
25%           0.058300         0.052500          0.044500           0.044100   
50%           0.087400         0.084000          0.076500           0.076100   
75%           0.149400         0.146000          0.112300           0.111800   
max           1.000000         1.000000          1.000000           1.000000   

       BASEMENTAREA_MODE   CNT_CHILDREN  CNT_FAM_MEMBERS  COMMONAREA_AVG  \
count      148671.000000  356255.000000    356253.000000   107895.000000   
mean            0.087750       0.414316         2.151858        0.045045   
std             0.084076       0.720378         0.907937        0.077045   
min             0.000000       0.000000         1.000000        0.000000   
25%             0.041000       0.000000         2.000000        0.007900   
50%             0.074900       0.000000         2.000000        0.021300   
75%             0.112700       1.000000         3.000000        0.051900   
max             1.000000      20.000000        21.000000        1.000000   

       COMMONAREA_MEDI  COMMONAREA_MODE     DAYS_BIRTH  DAYS_EMPLOYED 

In [99]:
# Compute correlations
corr_mat = feature_matrix_spec.corr()

In [129]:
# Get features whose correlations are too strong

threshold = 0.9

feat_corr = set()
corr_matrix = corr_mat
for i in range(len(corr_matrix.columns)):
    for j in range(i):
        if abs(corr_matrix.iloc[i,j]) > threshold:
            feat_name = corr_matrix.columns[i]
            feat_corr.add(feat_name)

In [131]:
feat_corr

{'AMT_GOODS_PRICE',
 'APARTMENTS_MEDI',
 'APARTMENTS_MODE',
 'BASEMENTAREA_MEDI',
 'BASEMENTAREA_MODE',
 'CODE_GENDER_M',
 'COMMONAREA_MEDI',
 'COMMONAREA_MODE',
 'COUNT(bureau)',
 'COUNT(bureau_balance)',
 'COUNT(credit)',
 'COUNT(installments)',
 'COUNT(previous)',
 'ELEVATORS_MEDI',
 'ELEVATORS_MODE',
 'ENTRANCES_MEDI',
 'ENTRANCES_MODE',
 'FLAG_EMP_PHONE',
 'FLAG_OWN_CAR_Y',
 'FLAG_OWN_REALTY_Y',
 'FLOORSMAX_MEDI',
 'FLOORSMAX_MODE',
 'FLOORSMIN_MEDI',
 'FLOORSMIN_MODE',
 'HOUSETYPE_MODE_block of flats',
 'LANDAREA_MEDI',
 'LANDAREA_MODE',
 'LIVINGAPARTMENTS_AVG',
 'LIVINGAPARTMENTS_MEDI',
 'LIVINGAPARTMENTS_MODE',
 'LIVINGAREA_AVG',
 'LIVINGAREA_MEDI',
 'LIVINGAREA_MODE',
 'MEAN(bureau.AMT_CREDIT_MAX_OVERDUE)',
 'MEAN(bureau.COUNT(bureau_balance))',
 'MEAN(bureau.MEAN(bureau_balance.MONTHS_BALANCE))',
 'MEAN(cash.CNT_INSTALMENT_FUTURE)',
 'MEAN(cash.MONTHS_BALANCE)',
 'MEAN(cash.SK_DPD)',
 'MEAN(cash.SK_ID_CURR)',
 'MEAN(credit.AMT_INST_MIN_REGULARITY)',
 'MEAN(credit.AMT_PAYMENT_

In [132]:
# Remove the "set_train" column

feat_corr.remove("set_train")

In [133]:
# Get feature values whose correlations are too weak

threshold2 = 0

feat_corr2 = set()
corr_matrix2 = corr_mat
for i in range(len(corr_matrix2.columns)):
    for j in range(i):
        if abs(corr_matrix2.iloc[i,j]) < threshold2:
            feat_name2 = corr_matrix2.columns[i]
            feat_corr2.add(feat_name2)

In [134]:
feat_corr2

set()

In [135]:
# Delete the feature values

feature_matrix_spec3 = feature_matrix_spec.drop(feat_corr, axis=1)

feature_matrix_spec3

AMT_ANNUITY  AMT_CREDIT  AMT_INCOME_TOTAL  \
SK_ID_CURR                                              
100001          20560.5    568800.0        135000.000   
100002          24700.5    406597.5        202500.000   
100003          35698.5   1293502.5        270000.000   
100004           6750.0    135000.0         67500.000   
100005          17370.0    222768.0         99000.000   
100006          29686.5    312682.5        135000.000   
100007          21865.5    513000.0        121500.000   
100008          27517.5    490495.5         99000.000   
100009          41301.0   1560726.0        171000.000   
100010          42075.0   1530000.0        360000.000   
100011          33826.5   1019610.0        112500.000   
100012          20250.0    405000.0        135000.000   
100013          69777.0    663264.0        202500.000   
100014          21177.0    652500.0        112500.000   
100015          10678.5    148365.0         38419.155   
100016           5881.5     80865.0         67500.000   
100017          28966.5    918468.0        225000.000   
100018          32778.0    773680.5        189000.000   
100019          20160.0    299772.0        157500.000   
100020          26149.5    509602.5        108000.000   
100021          13500.0    270000.0         81000.000   
100022           7875.0    157500.0        112500.000   
100023          17563.5    544491.0         90000.000   
100024          21375.0    427500.0        135000.000   
100025          37561.5   1132573.5        202500.000   
100026          32521.5    497520.0        450000.000   
100027          23850.0    239850.0         83250.000   
100028          49018.5   1575000.0        315000.000   
100029          12703.5    247500.0        135000.000   
100030          11074.5    225000.0         90000.000   
...                 ...         ...               ...   
456226          34969.5    500566.5        225000.000   
456227          16479.0    247275.0         99000.000   
456228          35617.5    545040.0        540000.000   
456229           9000.0    180000.0        270000.000   
456230          18283.5    355536.0        292500.000   
456231          31473.0   1071909.0        117000.000   
456232          13351.5    135000.0        157500.000   
456233          23089.5    521280.0        225000.000   
456234           9148.5    135000.0         81000.000   
456235          31522.5   1078200.0         90000.000   
456236          43443.0   1575000.0        585000.000   
456237          37678.5    946764.0        135000.000   
456238          46858.5    479700.0        270000.000   
456239          23773.5    808650.0        180000.000   
456240          16875.0    337500.0        360000.000   
456241          12028.5    270126.0        180000.000   
456242          52168.5   1312110.0        198000.000   
456243          12694.5    225000.0         81000.000   
456244          35982.0   1303812.0        261000.000   
456245          11871.0    269550.0         81000.000   
456246          10620.0    225000.0         94500.000   
456247          17770.5    345510.0        112500.000   
456248          16096.5    331920.0        153000.000   
456249          22050.0    225000.0        112500.000   
456250          24709.5    312768.0        135000.000   
456251          27558.0    254700.0        157500.000   
456252          12001.5    269550.0         72000.000   
456253          29979.0    677664.0        153000.000   
456254          20205.0    370107.0        171000.000   
456255          49117.5    675000.0        157500.000   

            AMT_REQ_CREDIT_BUREAU_DAY  AMT_REQ_CREDIT_BUREAU_HOUR  \
SK_ID_CURR                                                          
100001                            0.0                         0.0   
100002                            0.0                         0.0   
100003                            0.0                         0.0   
100004                            0.0                         0.0   
100005

In [136]:
# Split the concatenated dataset into the train dataset and the test dataset
train_input3 = feature_matrix_spec3[feature_matrix_spec3.set_train==1].copy()
test_input3 = feature_matrix_spec3[feature_matrix_spec3.set_train==0].copy()

X3 = train_input3.drop("TARGET",axis=1).values
y3 = train_input3.loc[:,'TARGET'].values

# LightGBM
lgbm_train3 = lgbm.Dataset(X3,y3)
lgbm_eval3 = lgbm.Dataset(X3, y3, reference=lgbm_train3)

model3 = lgbm.train(lgbm_params, lgbm_train3, valid_sets=lgbm_eval3)


# Predict the test dataset
y_pred3 = model3.predict(X3)

# Compute the AUC
roc_auc_score(y3,y_pred3)

[1]	valid_0's binary_logloss: 0.253793
[2]	valid_0's binary_logloss: 0.251117
[3]	valid_0's binary_logloss: 0.24961
[4]	valid_0's binary_logloss: 0.24851
[5]	valid_0's binary_logloss: 0.248288
[6]	valid_0's binary_logloss: 0.247926
[7]	valid_0's binary_logloss: 0.247738
[8]	valid_0's binary_logloss: 0.247463
[9]	valid_0's binary_logloss: 0.2474
[10]	valid_0's binary_logloss: 0.247329
[11]	valid_0's binary_logloss: 0.247361
[12]	valid_0's binary_logloss: 0.247399
[13]	valid_0's binary_logloss: 0.247303
[14]	valid_0's binary_logloss: 0.247194
[15]	valid_0's binary_logloss: 0.247145
[16]	valid_0's binary_logloss: 0.247138
[17]	valid_0's binary_logloss: 0.247105
[18]	valid_0's binary_logloss: 0.24707
[19]	valid_0's binary_logloss: 0.246952
[20]	valid_0's binary_logloss: 0.246946
[21]	valid_0's binary_logloss: 0.246943
[22]	valid_0's binary_logloss: 0.246962
[23]	valid_0's binary_logloss: 0.246955
[24]	valid_0's binary_logloss: 0.246968
[25]	valid_0's binary_logloss: 0.246966
[26]	valid_0's

0.7643618025071093

In [137]:
# Predict the test dataset
y_test_pred3 = model3.predict(test_input3.values, num_iteration=model3.best_iteration)

# Submittion the result
sub['TARGET'] = y_test_pred3

sub.to_csv('"Home Credit Default Risk"_pipeline2-2.csv', index=False)

In [4]:
# Compute the feature importances

importances = 

SyntaxError: invalid syntax (<ipython-input-4-6da80a7f24f4>, line 3)